In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import sys
import os
import process_data

In [2]:
parent_dir = os.path.abspath(os.path.join(os.getcwd(), ".."))
sys.path.append(parent_dir)

In [3]:
interpolated_dir = os.path.join(parent_dir, "dataset_interpolated_fixed")

In [4]:
features = ["score_difference", "relative_strength", "type.id", "home_has_possession", "end.down", "end.yardsToEndzone", "end.distance", "field_position_shift", "home_timeouts_left", "away_timeouts_left"]

In [6]:
# Reload modules
import sys
import importlib
modules_to_reload = [
    'process_data',
]
for module_name in modules_to_reload:
    if module_name in sys.modules:
        del sys.modules[module_name]

import process_data

training_data = process_data.load_data(interpolated_dir, 
                                       years = [2016, 2017, 2018, 2019, 2020, 2021, 2022], 
                                       history_length = 4, 
                                       features = features, 
                                       label_feature = "final_score_difference")
validation_data = process_data.load_data(interpolated_dir, 
                                       years = [2023], 
                                       history_length = 4, 
                                       features = features, 
                                       label_feature = "final_score_difference")

test_data = process_data.load_data(interpolated_dir, 
                                       years = [2024], 
                                       history_length = 4, 
                                       features = features, 
                                       label_feature = "final_score_difference")


Loading data for 2022
  Processing 271 CSV files in parallel with 8 workers...
  Completed processing 2022
Loading data for 2024
skipping  2024
Loading data for 2023
skipping  2023
Loading data for .DS_Store
Loading data for 2017
  Processing 254 CSV files in parallel with 8 workers...
  NaN found in file: /Users/aly/Documents/University_of_Waterloo/Winter 2025/Research/code/NFL/ML/dataset_interpolated_fixed/2017/game_400951752.csv
  NaN found in file: /Users/aly/Documents/University_of_Waterloo/Winter 2025/Research/code/NFL/ML/dataset_interpolated_fixed/2017/game_400951752.csv
  NaN found in file: /Users/aly/Documents/University_of_Waterloo/Winter 2025/Research/code/NFL/ML/dataset_interpolated_fixed/2017/game_400951752.csv
  NaN found in file: /Users/aly/Documents/University_of_Waterloo/Winter 2025/Research/code/NFL/ML/dataset_interpolated_fixed/2017/game_400951752.csv
  NaN found in file: /Users/aly/Documents/University_of_Waterloo/Winter 2025/Research/code/NFL/ML/dataset_interpolate

In [7]:

for key in training_data.keys():
    if key > 0.99:
        print("Timestep {}".format(key))
        print(training_data[key])

Timestep 0.995
[{'rows': array([[-10.    ,   0.6573,   5.    ,   0.    ,   1.    ,  14.    ,
         12.    ,  -4.    ,   0.    ,   2.    ],
       [-10.    ,   0.6573,   5.    ,   0.    ,   2.    ,  15.    ,
         12.    ,   1.    ,   0.    ,   2.    ],
       [-10.    ,   0.6573,   5.    ,   0.    ,   2.    ,  15.    ,
         12.    ,   1.    ,   0.    ,   2.    ],
       [-10.    ,   0.6573,   5.    ,   0.    ,   3.    ,  16.    ,
         12.    ,   1.    ,   0.    ,   2.    ],
       [-10.    ,   0.6573,   5.    ,   0.    ,   3.    ,  16.    ,
         12.    ,   1.    ,   0.    ,   2.    ]], dtype=float32), 'label': -10.0}, {'rows': array([[-1.    ,  0.5967,  5.    ,  0.    ,  3.    , 18.    , 10.    ,
         2.    ,  1.    ,  2.    ],
       [-1.    ,  0.5967, 21.    ,  0.    ,  3.    , 19.    ,  7.    ,
         0.    ,  1.    ,  2.    ],
       [-1.    ,  0.5967,  5.    ,  0.    ,  1.    , 12.    , 11.    ,
        -7.    ,  0.    ,  2.    ],
       [-1.    ,  0.5967, 

In [ ]:
%load_ext autoreload
%autoreload 2

In [28]:
%reload_ext autoreload
from models.metric_learning import siamese_lstm
from models.metric_learning import kernel_knn


# Now use the reloaded module
kernel_knn.setup_lstm_models(training_data, validation_data, num_models=201, epochs=50, hidden_dim=32, sequence_length=5)

Training set shape: (3244, 5, 10), Validation set shape: (526, 5, 10)
Training for timestep [0.0, 0.005]
Actual input dimension: 10
Using device: cpu
Computing similarity matrix LSTM pair construction...


/Users/aly/Documents/University_of_Waterloo/Winter 2025/Research/code/NFL_env/lib/python3.9/site-packages/torch/nn/modules/rnn.py:123: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.3 and num_layers=1
  warnings.warn(


Created 81100 pairs
Sequence shape: torch.Size([3244, 5, 10])
LSTM data loaded!
Computing similarity matrix LSTM pair construction...


ValueError: Sample larger than population or is negative

In [ ]:
modules_to_reload = [
    'models.metric_learning.siamese_lstm',
    'models.metric_learning.kernel_knn',
]

for module_name in modules_to_reload:
    if module_name in sys.modules:
        del sys.modules[module_name]

In [ ]:
from models.metric_learning.siamese_lstm import SiameseLSTMClassifier
models = {} # keys is start_time-end_time, values is model
for model_path in os.listdir("saved_models_lstm"):
    if model_path.endswith(".pth"):
        model = SiameseLSTMClassifier.load_model(os.path.join("saved_models_lstm", model_path))
        timestep = float(model_path.split("_")[3].split("-")[0])
        print(timestep)
        models[timestep] = model # Model name looks like: siamese_model_LSTM_0.0-0.01_ep11_valAcc0.5402666666666667_valLoss0.7629.pth



Transformer Model loaded from: saved_models_transformer/siamese_model_Transformer_0.065-0.07_ep21_valAcc0.519_valLoss0.754.pth
Best epoch: 0.065, Val Acc: 0.5194
0.065
Transformer Model loaded from: saved_models_transformer/siamese_model_Transformer_0.445-0.45_ep1_valAcc0.602_valLoss0.683.pth
Best epoch: 0.445, Val Acc: 0.6021
0.445
Transformer Model loaded from: saved_models_transformer/siamese_model_Transformer_0.09-0.095_ep9_valAcc0.510_valLoss0.758.pth
Best epoch: 0.09, Val Acc: 0.5104
0.09
Transformer Model loaded from: saved_models_transformer/siamese_model_Transformer_0.665-0.67_ep2_valAcc0.669_valLoss0.624.pth
Best epoch: 0.665, Val Acc: 0.6687
0.665
Transformer Model loaded from: saved_models_transformer/siamese_model_Transformer_0.575-0.58_ep2_valAcc0.645_valLoss0.650.pth
Best epoch: 0.575, Val Acc: 0.6446
0.575
Transformer Model loaded from: saved_models_transformer/siamese_model_Transformer_0.72-0.725_ep2_valAcc0.684_valLoss0.591.pth
Best epoch: 0.72, Val Acc: 0.6838
0.72
T

In [ ]:
# Embed the training data
import faiss
import pickle
os.makedirs("saved_indexes_lstm", exist_ok=True)
for timestep in models.keys():
    print(f"Embedding data for timesteps {timestep}")
    relevant_data = []
    for timestep_key in training_data.keys():
        if timestep_key == timestep:
            for row in training_data[timestep_key]:
                relevant_data.append(row)
    model = models[timestep]
    # Embed the test data
    embeddings, labels = model.embed_data(relevant_data)
    embeddings = embeddings.cpu().numpy() # Needed by FAISS
    embeddings = embeddings.astype(np.float32)
    for i in range(len(labels)):
        if labels[i] > 0:
            labels[i] = 1
        else:
            labels[i] = 0
    with open(f"saved_indexes_lstm/metadata_{timestep}.pkl", "wb") as f:
        pickle.dump(labels, f)
    # Create FAISS index for each timesteps
    index = faiss.IndexFlatL2(embeddings.shape[1])
    index.add(embeddings)
    faiss.write_index(index, f"saved_indexes_lstm/faiss_index_{timestep}.faiss")
    print(f"FAISS index for timesteps {timestep} created")




# Save the FAISS index

Embedding data for timesteps 0.065
FAISS index for timesteps 0.065 created
Embedding data for timesteps 0.445
FAISS index for timesteps 0.445 created
Embedding data for timesteps 0.09
FAISS index for timesteps 0.09 created
Embedding data for timesteps 0.665
FAISS index for timesteps 0.665 created
Embedding data for timesteps 0.575
FAISS index for timesteps 0.575 created
Embedding data for timesteps 0.72
FAISS index for timesteps 0.72 created
Embedding data for timesteps 0.06
FAISS index for timesteps 0.06 created
Embedding data for timesteps 0.83
FAISS index for timesteps 0.83 created
Embedding data for timesteps 0.82
FAISS index for timesteps 0.82 created
Embedding data for timesteps 0.29
FAISS index for timesteps 0.29 created
Embedding data for timesteps 0.175
FAISS index for timesteps 0.175 created
Embedding data for timesteps 0.12
FAISS index for timesteps 0.12 created
Embedding data for timesteps 0.775
FAISS index for timesteps 0.775 created
Embedding data for timesteps 0.155
FAIS

In [ ]:
indexes = {}
metadata = {}
from pathlib import Path
for index_path in os.listdir("saved_indexes_lstm"):
    if index_path.endswith(".faiss"):
        index = faiss.read_index(os.path.join("saved_indexes_lstm", index_path))
        timestep = float(Path(index_path).stem.split("_")[2])
        indexes[timestep] = index
    elif index_path.endswith(".pkl"):
        with open(os.path.join("saved_indexes_lstm", index_path), "rb") as f:
            timestep = float(Path(index_path).stem.split("_")[1])
            metadata[timestep] = pickle.load(f)



In [89]:
# Retrieval
def get_prediction(entry, model, timestep, indexes, metadata, k=10):
    """
    Args:
        entry: torch.Tensor of shape (1, input_dim)
        model: SiameseClassifier
        timestep: intIndex
        indexes: dict mapping timestep -> faiss.
        metadata: dict mapping timestep -> np.array of labels (floats, shape (N,))
        k: int, number of neighbors to retrieve
    Returns:
        prediction: float in [0, 1]
    """
    # Normalize entry for cosine similarity
    embedding = model.embed(entry).unsqueeze(0)
    index = indexes[timestep]
    labels = metadata[timestep]
    
    # FAISS expects (n_queries, d)
    # FAISS inner product = cosine sim IF vectors are normalized
    distances, indices = index.search(embedding, k)
    indices = indices[0]  # shape (k,)
    similarities = distances[0]  # shape (k,)

    # Some neighbors may be -1 (if <k vectors in index)
    mask = indices != -1
    indices = indices[mask]
    similarities = similarities[mask]

    # Get their labels
    neighbor_labels = np.array([labels[i] for i in indices])
    # Similarities may be negative if entry is not similar; clamp to >=0 for weights
    similarities = np.clip(similarities, 0, None)

    if similarities.sum() == 0:
        # Fallback: unweighted mean
        prediction = neighbor_labels.mean() if len(neighbor_labels) > 0 else 0.0
    else:
        # Weighted average
        prediction = np.dot(similarities, neighbor_labels) / similarities.sum()

    # Clamp prediction to [0, 1]
    prediction = float(np.clip(prediction, 0, 1))
    return prediction


In [ ]:
import os
import pandas as pd
import numpy as np
import torch
from models.metric_learning.siamese_network import SiameseClassifier


def write_predictions(models, interpolated_dir, years, history_length, features, replace_nan_val = 0, phat_b = "phat_b"):
    # Write the predictions to csv file
    for folder in os.listdir(interpolated_dir):
        folder_path = os.path.join(interpolated_dir, folder)
        if os.path.isdir(folder_path):
            if (int(folder) in years):
                print(f"Loading data for {folder}")
                for file in os.listdir(folder_path):
                    if file.endswith(".csv"):
                        file_path = os.path.join(folder_path, file)
                        df = pd.read_csv(file_path)
                        df.loc[1:, "relative_strength"] = df.iloc[0]["homeWinProbability"]
                        df.loc[1:, "away_team_id"] = df.iloc[0]["away_team_id"]
                        df.loc[1:, "home_team_id"] = df.iloc[0]["home_team_id"]
                        df.loc[1:, "home_win"] = df.iloc[0]["home_win"]
                        for idx in range(1, len(df)):
                            current_row = df.iloc[idx]
                            # Get column names
                            current_row_features = current_row[features].to_numpy(dtype=np.float32)
                            current_row_features = np.nan_to_num(current_row_features, nan=replace_nan_val)
                            
                            current_row_np = current_row_features.reshape(1, -1)
                            start_idx = max(1, idx - history_length)
                            actual_history_len = idx - start_idx
                            if history_length > 0:
                                history_rows = df.iloc[start_idx:idx][features].to_numpy(dtype=np.float32)
                                history_rows = np.nan_to_num(history_rows, nan=replace_nan_val)
                                if actual_history_len < history_length:
                                    padding = np.zeros((history_length - actual_history_len, len(features)))
                                    history_rows = np.concatenate([padding, history_rows], axis=0)
                                final_rows_for_timestep = np.concatenate([history_rows, current_row_np], axis=0)
                            else:
                                final_rows_for_timestep = current_row_np.reshape(-1)
                            # Do inference
                            timestep = round(current_row["timestep"], 3)
                            model = models[timestep]
                            X_test = final_rows_for_timestep.reshape(1, -1)
                            X_test = torch.FloatTensor(X_test)
                            pred = get_prediction(X_test, model, timestep, indexes, metadata)
                            df.at[idx, phat_b] = pred
                        df.to_csv(file_path, index=False)
                        print("Processed file: ", file)

write_predictions(models, interpolated_dir, [2023, 2024], 0, features, replace_nan_val = 0, phat_b = "siamese_network_phat_b")


Loading data for 2024
Processed file:  game_401671629.csv
Processed file:  game_401671601.csv
Processed file:  game_401671826.csv
Processed file:  game_401671832.csv
Processed file:  game_401671749.csv
Processed file:  game_401671775.csv
Processed file:  game_401671761.csv
Processed file:  game_401671760.csv
Processed file:  game_401671774.csv
Processed file:  game_401671748.csv
Processed file:  game_401671833.csv
Processed file:  game_401671827.csv
Processed file:  game_401671600.csv
Processed file:  game_401671628.csv
Processed file:  game_401671616.csv
Processed file:  game_401671831.csv
Processed file:  game_401671825.csv
Processed file:  game_401671819.csv
Processed file:  game_401671762.csv
Processed file:  game_401671776.csv
Processed file:  game_401671789.csv
Processed file:  game_401671788.csv
Processed file:  game_401671777.csv
Processed file:  game_401671763.csv
Processed file:  game_401671818.csv
Processed file:  game_401671824.csv
Processed file:  game_401671830.csv
Proces